In [1]:
import pandas as pd
from Utils import calcular_resultados

In [2]:
dataset = pd.read_csv('dataset//Teste_JBCS25.csv')

In [5]:
def selecionar_index(dataset):
    index_a = []
    index_b = []
    for index, row in dataset.iterrows():
        if row['reference'] == 'grader_a':
            index_a.append(index)
        elif row['reference'] == 'grader_b':
            index_b.append(index)
        else:
            print("Erro")
    assert len(index_a) == len(index_b)
    return index_a, index_b
index_a, index_b = selecionar_index(dataset)

In [7]:
print(index_a)
print(index_b)

[0, 1, 5, 7, 8, 11, 12, 14, 15, 17, 19, 21, 23, 25, 26, 27, 29, 33, 38, 39, 43, 44, 45, 46, 48, 49, 52, 53, 56, 57, 58, 59, 61, 62, 65, 67, 69, 70, 73, 75, 79, 82, 86, 91, 92, 94, 96, 98, 99, 100, 101, 102, 103, 105, 108, 113, 114, 117, 118, 119, 122, 123, 125, 126, 128, 133, 135, 136, 137]
[2, 3, 4, 6, 9, 10, 13, 16, 18, 20, 22, 24, 28, 30, 31, 32, 34, 35, 36, 37, 40, 41, 42, 47, 50, 51, 54, 55, 60, 63, 64, 66, 68, 71, 72, 74, 76, 77, 78, 80, 81, 83, 84, 85, 87, 88, 89, 90, 93, 95, 97, 104, 106, 107, 109, 110, 111, 112, 115, 116, 120, 121, 124, 127, 129, 130, 131, 132, 134]


In [11]:
def quebrar_respostas(y, y_hat, index_a, index_b):
    y_hat_a = []
    y_hat_b = []
    y_a, y_b = [], []
    #print(y)
    for idx in range(len(y)):
        if idx in index_a:
            y_a.append( y[idx] )
            y_hat_a.append( y_hat[idx] )
        elif idx in index_b:
            y_b.append( y[idx] )
            y_hat_b.append( y_hat[idx] )
        elif (idx in index_a) and (idx in index_b):
            print("Erro")
    return y_a, y_b, y_hat_a, y_hat_b

def formatar_respostas(dic_a, dic_b, dic_geral):
    F1_m_a = sum(dic_a['F1-Macro'])/len(dic_a['F1-Macro'])
    F1_w_a = sum(dic_a['F1-Weighted'])/len(dic_a['F1-Weighted'])
    QWK_a = sum(dic_a['QWK'])/len(dic_a['QWK'])
    print(f"A: {F1_m_a:.2f} & {F1_w_a:.2f} & {QWK_a:.2f} &")
    F1_m_b = sum(dic_b['F1-Macro'])/len(dic_b['F1-Macro'])
    F1_w_b = sum(dic_b['F1-Weighted'])/len(dic_b['F1-Weighted'])
    QWK_b = sum(dic_b['QWK'])/len(dic_b['QWK'])
    print(f"B: {F1_m_b:.2f} & {F1_w_b:.2f} & {QWK_b:.2f} &")
    F1_m_geral = sum(dic_geral['F1-Macro'])/len(dic_geral['F1-Macro'])
    F1_w_geral = sum(dic_geral['F1-Weighted'])/len(dic_geral['F1-Weighted'])
    QWK_geral = sum(dic_geral['QWK'])/len(dic_geral['QWK'])
    print(f"geral: {F1_m_geral:.2f} & {F1_w_geral:.2f} & {QWK_geral:.2f} &")
    F1_m_media = (F1_m_a + F1_m_b) / 2
    F1_w_media = (F1_w_a + F1_w_b) / 2 
    QWK_media =  (QWK_a + QWK_b) / 2
    print(f"media: {F1_m_media:.2f} & {F1_w_media:.2f} & {QWK_media:.2f} &")

def adicionar_performances(dic_a, dic_b, dic_geral, perf_a, perf_b, perf_geral):
    for key in perf_a:
        perf_a[key].append(dic_a[key])
        perf_b[key].append(dic_b[key])
        perf_geral[key].append(dic_geral[key])
    
def calcular_media(dataset, index_a, index_b):
    perf_a = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    perf_b = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    perf_geral = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    for idx, row in dataset.iterrows():
        y = eval(row['y'])
        y_hat = eval(row['y_hat'])
        y_a, y_b, y_hat_a, y_hat_b = quebrar_respostas(y, y_hat, index_a, index_b)
        dic_a = calcular_resultados(y_a, y_hat_a)
        dic_b = calcular_resultados(y_b, y_hat_b)
        dic_geral = calcular_resultados(y_a + y_b, y_hat_a + y_hat_b)
        adicionar_performances(dic_a, dic_b, dic_geral, perf_a, perf_b, perf_geral)
    formatar_respostas(perf_a, perf_b, perf_geral)

In [13]:
"""
for comp in range(1, 6):
    print(f"Comp {comp}")
    respostas = pd.read_csv(f'RF-{comp}.csv')
    calcular_media(respostas, index_a, index_b)
"""

'\nfor comp in range(1, 6):\n    print(f"Comp {comp}")\n    respostas = pd.read_csv(f\'RF-{comp}.csv\')\n    calcular_media(respostas, index_a, index_b)\n'

In [27]:
def calcular_media(dataset, index_a, index_b, nome):
    global Y_HAT, NORMALIZACAO
    perf_a = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    perf_b = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    perf_geral = {'QWK': [], 'F1-Macro': [], 'F1-Weighted': []}
    y = (dataset['label']*NORMALIZACAO).tolist()
    y_hat = (dataset[Y_HAT]*NORMALIZACAO).tolist()
    y_a, y_b, y_hat_a, y_hat_b = quebrar_respostas(y, y_hat, index_a, index_b)
    dic_a = calcular_resultados(y_a, y_hat_a)
    dic_b = calcular_resultados(y_b, y_hat_b)
    dic_geral = calcular_resultados(y_a + y_b, y_hat_a + y_hat_b)
    adicionar_performances(dic_a, dic_b, dic_geral, perf_a, perf_b, perf_geral)
    formatar_respostas(perf_a, perf_b, perf_geral, nome)



def printar_dic(dic, nome):
    global dic_print_global
    F1_m = sum(dic['F1-Macro'])/len(dic['F1-Macro'])
    F1_w = sum(dic['F1-Weighted'])/len(dic['F1-Weighted'])
    QWK = sum(dic['QWK'])/len(dic['QWK'])
    print_A = f"{F1_m:.2f} & {F1_w:.2f} & {QWK:.2f} &"
    print(f"{nome}: {print_A}")
    dic_print_global[nome] += print_A

def fazer_media(dic1, dic2):
    F1_macro = (dic1['F1-Macro'][0]+dic2['F1-Macro'][0])/2
    F1_weighted = (dic1['F1-Weighted'][0]+dic2['F1-Weighted'][0])/2
    #print(dic1['QWK'], dic2['QWK'])
    QWK = (dic1['QWK'][0]+dic2['QWK'][0])/2
    return {'F1-Macro': [F1_macro], 'F1-Weighted': [F1_weighted], 'QWK': [QWK]}

def formatar_respostas(dic_a, dic_b, dic_geral, nome):
    global dic_print_global
    printar_dic(dic_a, f"{nome}-A")
    printar_dic(dic_b, f"{nome}-B")
    printar_dic(dic_geral, f"{nome}-geral")
    printar_dic(fazer_media(dic_a, dic_b), f"{nome}-media")
    """
    print(f"A: {print_A})
    dic_print_global[f"{nome}-A"
    F1_m_b = sum(dic_b['F1-Macro'])/len(dic_b['F1-Macro'])
    F1_w_b = sum(dic_b['F1-Weighted'])/len(dic_b['F1-Weighted'])
    QWK_b = sum(dic_b['QWK'])/len(dic_b['QWK'])
    print(f"B: {F1_m_b:.2f} & {F1_w_b:.2f} & {QWK_b:.2f} &")
    F1_m_geral = sum(dic_geral['F1-Macro'])/len(dic_geral['F1-Macro'])
    F1_w_geral = sum(dic_geral['F1-Weighted'])/len(dic_geral['F1-Weighted'])
    QWK_geral = sum(dic_geral['QWK'])/len(dic_geral['QWK'])
    print(f"geral: {F1_m_geral:.2f} & {F1_w_geral:.2f} & {QWK_geral:.2f} &")
    F1_m_media = (F1_m_a + F1_m_b) / 2
    F1_w_media = (F1_w_a + F1_w_b) / 2 
    QWK_media =  (QWK_a + QWK_b) / 2
    print(f"media: {F1_m_media:.2f} & {F1_w_media:.2f} & {QWK_media:.2f} &")
    """

dic_print_global = {}
def gerar_nome(modelo, comp):
    global dic_print_global
    string = ""
    if modelo == 'bertimbau-base':
        string = f"jbcs2025_bertimbau_base-C{comp}-encoder_classification-C{comp}_inference_results.jsonl"
    elif modelo == 'mbert':
        string = f'jbcs2025_mbert_base-C{comp}-encoder_classification-C{comp}_inference_results.jsonl'
    elif modelo == 'bertimbau-large':
        string = f"jbcs2025_bertimbau-large-C{comp}-encoder_classification-C{comp}_inference_results.jsonl"
    elif modelo == "Llama-essay_only":
        string = f"jbcs2025_llama31_8b-balanced-C{comp}-llama31_classification_lora-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "Llama-full_context":
        string = f"jbcs2025_Llama-3.1-8B-llama31_classification_lora-C{comp}-full_context-llama31_classification_lora-C{comp}-full_context_inference_results.jsonl"
    elif modelo == "Phi4-essay_only":
        string = f"jbcs2025_phi4-balanced-C{comp}-phi4_classification_lora-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "Phi4-full_context":
        string = f"jbcs2025_phi-4-phi4_classification_lora-C{comp}-full_context-phi4_classification_lora-C{comp}-full_context_inference_results.jsonl"
    elif modelo == "Phi3.5-essay-only":
        string = f"jbcs2025_phi35-balanced-C{comp}-phi35_classification_lora-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "Phi3.5-full_context":
        string = f"jbcs2025_Phi-3.5-mini-instruct-phi35_classification_lora-C{comp}-full_context-phi35_classification_lora-C{comp}-full_context_inference_results.jsonl"
    #sabias
    elif modelo == "sabia-essay-only":
        string = f"sabia-3-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "sabia-full":
        string = f"sabia-3-zero-shot-C{comp}-full_context_inference_results.jsonl"
    elif modelo == "sabia-grader-full":
        string = f"sabia-3-grader-zero-shot-C{comp}-full_context_inference_results.jsonl"
    elif modelo == "sabia-grader-essay-only":
        string = f"sabia-3-grader-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "sabia-extractor-full":
        string = f"sabia-3-extractor-zero-shot-C{comp}-full_context_inference_results.jsonl"
    #gpts
    elif modelo == 'gpt4-essay-only':
        string = f"gpt-4o-2024-11-20-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == 'gpt4-full':
        string = f"gpt-4o-2024-11-20-zero-shot-C{comp}-full_context_inference_results.jsonl"
    elif modelo == 'gpt4-grader-full':
        string = f"gpt-4o-2024-11-20-zero-shot-grader-C{comp}-full_context_inference_results.jsonl"
    elif modelo == 'gpt4-grader-essay-only':
        string = f"gpt-4o-2024-11-20-grader-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    #deepseeks
    elif modelo == 'deepseek-essay-only':
        string = f"deepseek-reasoner-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == 'deepseek-full':
        string = f"deepseek-reasoner-zero-shot-C{comp}-full_context_inference_results.jsonl"
    elif modelo == 'deepseek-grader-essay-only':
        string = f"deepseek-reasoner-grader-zero-shot-C{comp}-essay_only_inference_results.jsonl"
    elif modelo == "deepseek-grader-full-context":
        string = f"deepseek-reasoner-grader-zero-shot-C{comp}-full_context_inference_results.jsonl"
    elif modelo == "deepseek-extractor-full-context":
        string = f"deepseek-reasoner-extractor-zero-shot-C{comp}-full_context_inference_results.jsonl"
    if comp == 1:
        dic_print_global[f"{modelo}-A"] = ""
        dic_print_global[f"{modelo}-B"] = ""
        dic_print_global[f"{modelo}-geral"] = ""
        dic_print_global[f"{modelo}-media"] = ""
    return string

In [29]:
#print(f"Comp C1")
modelo = 'sabia-extractor-full'
Y_HAT = "pontuacao"
NORMALIZACAO = 1
for comp in range(1, 6):
    #print(comp)
    nome = gerar_nome(modelo, comp)
    respostas = pd.read_json(nome, lines=True)
    #print(respostas.head())
    calcular_media(respostas, index_a, index_b, modelo)

sabia-extractor-full-A: 0.09 & 0.24 & 0.29 &
sabia-extractor-full-B: 0.11 & 0.28 & 0.33 &
sabia-extractor-full-geral: 0.09 & 0.26 & 0.31 &
sabia-extractor-full-media: 0.10 & 0.26 & 0.31 &
sabia-extractor-full-A: 0.21 & 0.34 & 0.29 &
sabia-extractor-full-B: 0.12 & 0.14 & 0.27 &
sabia-extractor-full-geral: 0.15 & 0.21 & 0.28 &
sabia-extractor-full-media: 0.16 & 0.24 & 0.28 &
sabia-extractor-full-A: 0.20 & 0.37 & 0.24 &
sabia-extractor-full-B: 0.20 & 0.21 & 0.19 &
sabia-extractor-full-geral: 0.19 & 0.27 & 0.21 &
sabia-extractor-full-media: 0.20 & 0.29 & 0.21 &
sabia-extractor-full-A: 0.19 & 0.42 & 0.35 &
sabia-extractor-full-B: 0.18 & 0.35 & 0.40 &
sabia-extractor-full-geral: 0.17 & 0.38 & 0.38 &
sabia-extractor-full-media: 0.18 & 0.38 & 0.38 &
sabia-extractor-full-A: 0.22 & 0.25 & 0.46 &
sabia-extractor-full-B: 0.21 & 0.23 & 0.56 &
sabia-extractor-full-geral: 0.23 & 0.23 & 0.52 &
sabia-extractor-full-media: 0.22 & 0.24 & 0.51 &


In [31]:
for key in dic_print_global:
    print(f"{key} & {dic_print_global[key][:-2] } \\\\")

sabia-extractor-full-A & 0.09 & 0.24 & 0.29 &0.21 & 0.34 & 0.29 &0.20 & 0.37 & 0.24 &0.19 & 0.42 & 0.35 &0.22 & 0.25 & 0.46 \\
sabia-extractor-full-B & 0.11 & 0.28 & 0.33 &0.12 & 0.14 & 0.27 &0.20 & 0.21 & 0.19 &0.18 & 0.35 & 0.40 &0.21 & 0.23 & 0.56 \\
sabia-extractor-full-geral & 0.09 & 0.26 & 0.31 &0.15 & 0.21 & 0.28 &0.19 & 0.27 & 0.21 &0.17 & 0.38 & 0.38 &0.23 & 0.23 & 0.52 \\
sabia-extractor-full-media & 0.10 & 0.26 & 0.31 &0.16 & 0.24 & 0.28 &0.20 & 0.29 & 0.21 &0.18 & 0.38 & 0.38 &0.22 & 0.24 & 0.51 \\
